In [62]:
import gzip
import math
import random
from collections import defaultdict
import json
import ast
from collections import Counter
from operator import itemgetter
import numpy as np

import matplotlib.pyplot as plt
import random
from random import choices
random.seed(10)

In [35]:
user_list = []
f = open('australian_users_items_double_quotes.json', encoding="utf8")
for line in f:
       
    cur_json = json.loads(line)
    user_list.append(cur_json)

### Create train and test without considering playtime

In [36]:
user_item_list = []
for user in user_list:
    for item in user['items']:
        user_item_list.append((user['user_id'],item['item_id']))

In [38]:
random.shuffle(user_item_list)

In [39]:
train = user_item_list[:4000000]
test = user_item_list[4000000:][:500000]

In [40]:
print(f"Number of train is {len(train)}")
print(f"Number of test is {len(test)}")

Number of train is 4000000
Number of test is 500000


### Add false interaction to test data

In [41]:
#### Create dictionary
user_set = set([i[0] for i in user_item_list])
item_set = set([i[1] for i in user_item_list])
user_per_item = defaultdict(set)
item_per_user = defaultdict(set)


In [42]:
for user_item in user_item_list:
    user,item = user_item[0],user_item[1]
    user_per_item[item].add(user)
    item_per_user[user].add(item)
    

In [67]:
random.seed(10)
test_neg_user =  choices(list(user_set),k = 500000)

In [73]:
#### Maybe consider the distribution(popularity) of the game when sampling
random.sample(item_set,k = 1)

C:\Users\steve\AppData\Local\Temp\ipykernel_19752\2058216400.py:2: DeprecationWarning: Sampling from a set deprecated
since Python 3.9 and will be removed in a subsequent version.
  random.sample(item_set,k = 1)


['359850']

In [88]:
random.seed(10)
test_neg_entries = []
for user in test_neg_user:
    item_candidate = random.sample(item_set,k = 1)[0]
    temp = item_per_user[user]
    while item_candidate in temp:
        item_candidate = random.sample(item_set,k = 1)[0]
    test_neg_entries.append((user,item_candidate))


C:\Users\steve\AppData\Local\Temp\ipykernel_19752\1083373277.py:4: DeprecationWarning: Sampling from a set deprecated
since Python 3.9 and will be removed in a subsequent version.
  item_candidate = random.sample(item_set,k = 1)[0]
C:\Users\steve\AppData\Local\Temp\ipykernel_19752\1083373277.py:7: DeprecationWarning: Sampling from a set deprecated
since Python 3.9 and will be removed in a subsequent version.
  item_candidate = random.sample(item_set,k = 1)[0]


In [90]:
len(test_neg_entries)

500000

In [91]:
test_total = test+test_neg_entries

In [127]:
len(test_total)

1000000

In [128]:
test_total_y = [1]*500000+[0]*500000

In [171]:
####### Construct smaller testset for development###########
dev_train = train[:4000000]
dev_test = test[:500000]+test_neg_entries[:500000]
dev_test_y = [1]*500000 + [0]*500000

### Baseline Model (Popularity Based)

In [172]:
game_list = []
for i in dev_train:
    user,item = i[0],i[1]
    game_list.append(item)

In [173]:
game_count = Counter(game_list)
sorted_game = sorted(game_count.items(),key=itemgetter(1),reverse = True)

In [174]:
game_list_sorted = [i[0] for i in sorted_game]
############## DEFINE POPULAR GAME ################
popular_games = game_list_sorted[:5000]

In [175]:
baseline_pred = []
for i in dev_test:
    user,item = i[0],i[1]
    if item in popular_games:
        baseline_pred.append(1)
    else:
        baseline_pred.append(0)

In [176]:
baseline_acc = sum(1 for x,y in zip(dev_test_y,baseline_pred) if x == y) / len(baseline_pred)
baseline_acc

0.764519

### Similarity Based Model

In [177]:
def Jaccard(s1, s2):
    numer = len(s1.intersection(s2))
    denom = len(s1.union(s2))
    if denom == 0:
        return 0
    return numer / denom

In [178]:
##### Build dictionaries using train #####
dev_user_set = set([i[0] for i in dev_train])
dev_item_set = set([i[1] for i in dev_train])
dev_user_per_item = defaultdict(set)
dev_item_per_user = defaultdict(set)

In [179]:
for (user,item) in dev_train:
    dev_user_per_item[item].add(user)
    dev_item_per_user[user].add(item)

In [180]:
dev_item_per_user

defaultdict(set,
            {'76561197977174002': {'102840',
              '104600',
              '107100',
              '113200',
              '11450',
              '12120',
              '12210',
              '12330',
              '1250',
              '12710',
              '12810',
              '12830',
              '12840',
              '13200',
              '13230',
              '13250',
              '13510',
              '13620',
              '13630',
              '13640',
              '1510',
              '15100',
              '15120',
              '15130',
              '15190',
              '15200',
              '15210',
              '1530',
              '15300',
              '15620',
              '16810',
              '17300',
              '17330',
              '17340',
              '17410',
              '17460',
              '17470',
              '18700',
              '19800',
              '19900',
              '200510',
              '20

In [ ]:
maxSim_list = []
dev_pred = []
for (user,item) in dev_test:
    maxSim = 0
    users = set(dev_user_per_item[item])
    for item2 in dev_item_per_user[user]:
        sim = Jaccard(users,set(dev_user_per_item[item2]))
        if sim > maxSim:
            maxSim = sim
    pred = 0
    if maxSim > 0.013 or len(dev_user_per_item[item]) > 40:
        dev_pred.append(1)
    else:
        dev_pred.append(0)
#     maxSim_list.append(maxSim)


In [ ]:
dev_test_acc = sum(1 for x,y in zip(dev_test_y,dev_pred) if x == y) / len(dev_pred)
dev_test_acc